In [1]:
import polars as pl
import os
from datetime import datetime
from datetime import timezone
import plotly.express as px
import numpy as np

DATA_DIRECTORY = os.environ.get("DATA_DIRECTORY")
PICARRO_DATA_DIRECTORy = os.environ.get("PICARRO_DATA_DIRECTORY")

In [2]:
# 10m preprocessed acropolis data
df_acropolis = pl.scan_parquet(os.path.join(DATA_DIRECTORY, "processed", "filtered_1_std_acropolis.parquet"))

In [3]:
df_acropolis.tail(5).collect()

shape: (5, 69)
┌───────────┬───────────┬───────────┬───────────┬───┬───────────┬───────────┬───────────┬──────────┐
│ system_na ┆ sys_name_ ┆ creation_ ┆ gmp343_ra ┆ … ┆ mse_2_std ┆ rmse_full ┆ rmse_1_st ┆ rmse_2_s │
│ me        ┆ short     ┆ timestamp ┆ w         ┆   ┆ _full_dep ┆ _deployme ┆ d_full_de ┆ td_full_ │
│ ---       ┆ ---       ┆ ---       ┆ ---       ┆   ┆ loyment   ┆ nt        ┆ ployment  ┆ deployme │
│ str       ┆ str       ┆ datetime[ ┆ f64       ┆   ┆ ---       ┆ ---       ┆ ---       ┆ nt       │
│           ┆           ┆ μs, UTC]  ┆           ┆   ┆ f64       ┆ f64       ┆ f64       ┆ ---      │
│           ┆           ┆           ┆           ┆   ┆           ┆           ┆           ┆ f64      │
╞═══════════╪═══════════╪═══════════╪═══════════╪═══╪═══════════╪═══════════╪═══════════╪══════════╡
│ tum-esm-m ┆ mid-cost- ┆ 2024-02-1 ┆ 389.51165 ┆ … ┆ 0.689435  ┆ 0.830414  ┆ 0.829086  ┆ 0.830322 │
│ idcost-ra ┆ 20        ┆ 1         ┆ 7         ┆   ┆           ┆           ┆           ┆          │
│ spi-20    ┆           ┆ 19:00:00  ┆           ┆   ┆           ┆           ┆           ┆          │
│           ┆           ┆ UTC       ┆           ┆   ┆           ┆           ┆           ┆          │
│ tum-esm-m ┆ mid-cost- ┆ 2024-02-1 ┆ 390.69577 ┆ … ┆ 0.689435  ┆ 0.830414  ┆ 0.829086  ┆ 0.830322 │
│ idcost-ra ┆ 20        ┆ 1         ┆ 6         ┆   ┆           ┆           ┆           ┆          │
│ spi-20    ┆           ┆ 20:00:00  ┆           ┆   ┆           ┆           ┆           ┆          │
│           ┆           ┆ UTC       ┆           ┆   ┆           ┆           ┆           ┆          │
│ tum-esm-m ┆ mid-cost- ┆ 2024-02-1 ┆ 389.56587 ┆ … ┆ 0.689435  ┆ 0.830414  ┆ 0.829086  ┆ 0.830322 │
│ idcost-ra ┆ 20        ┆ 1         ┆ 1         ┆   ┆           ┆           ┆           ┆          │
│ spi-20    ┆           ┆ 21:00:00  ┆           ┆   ┆           ┆           ┆           ┆          │
│           ┆           ┆ UTC       ┆           ┆   ┆           ┆           ┆           ┆          │
│ tum-esm-m ┆ mid-cost- ┆ 2024-02-1 ┆ 389.38610 ┆ … ┆ 0.689435  ┆ 0.830414  ┆ 0.829086  ┆ 0.830322 │
│ idcost-ra ┆ 20        ┆ 1         ┆ 2         ┆   ┆           ┆           ┆           ┆          │
│ spi-20    ┆           ┆ 22:00:00  ┆           ┆   ┆           ┆           ┆           ┆          │
│           ┆           ┆ UTC       ┆           ┆   ┆           ┆           ┆           ┆          │
│ tum-esm-m ┆ mid-cost- ┆ 2024-02-1 ┆ 386.38050 ┆ … ┆ 0.689435  ┆ 0.830414  ┆ 0.829086  ┆ 0.830322 │
│ idcost-ra ┆ 20        ┆ 1         ┆ 3         ┆   ┆           ┆           ┆           ┆          │
│ spi-20    ┆           ┆ 23:00:00  ┆           ┆   ┆           ┆           ┆           ┆          │
│           ┆           ┆ UTC       ┆           ┆   ┆           ┆           ┆           ┆          │
└───────────┴───────────┴───────────┴───────────┴───┴───────────┴───────────┴───────────┴──────────┘

In [4]:
df_mean_deloyment = df_acropolis.group_by("system_name") \
    .agg([(pl.col("slope").mean()).alias("slope_mean_deployment"),
        (pl.col("intercept").mean()).alias("intercept_mean_deployment")
         ])
    
df_median_deloyment = df_acropolis.group_by("system_name") \
    .agg([(pl.col("slope").median()).alias("slope_median_deployment"),
        (pl.col("intercept").median()).alias("intercept_median_deployment")
         ]) 

In [5]:
df_filtered = df_acropolis.join(df_mean_deloyment, on = "system_name", how= "left") \
    .join(df_median_deloyment, on = "system_name", how= "left")

In [6]:
all_systems = []

system_list = df_filtered.collect()["system_id"].unique().to_list()

for id in system_list:
    print(f"processing {id}")

    df_temp = df_filtered.filter(pl.col("system_id") == id) \
            .with_columns([
            ((pl.col("gmp343_dry")) * pl.col("slope_mean_deployment") + pl.col("intercept_mean_deployment")).alias("gmp343_corrected_mean_deployment"),
            ((pl.col("gmp343_dry")) * pl.col("slope_median_deployment") + pl.col("intercept_median_deployment")).alias("gmp343_corrected_median_deployment")
                                ]) \
            .with_columns([
                (pl.col("CO2_corr") - pl.col("gmp343_corrected_mean_deployment")).alias("diff_1"),
                (pl.col("CO2_corr") - pl.col("gmp343_corrected_median_deployment")).alias("diff_2"),
                (np.square(np.subtract(pl.col("CO2_corr"), pl.col("gmp343_corrected_mean_deployment"))).mean()).alias("mse_mean_full_deployment"),
                (np.square(np.subtract(pl.col("CO2_corr"), pl.col("gmp343_corrected_median_deployment"))).mean()).alias("mse_median_full_deployment")
                        ]) \
            .with_columns([
                pl.col("mse_mean_full_deployment").sqrt().alias("rmse_mean_deployment"),
                pl.col("mse_median_full_deployment").sqrt().alias("rmse_median_deployment")
                        ]) \
            .collect()
            
    all_systems.append(df_temp)
    
df_all_filtered = pl.concat(all_systems, how="diagonal")

processing 1.0
processing 3.0
processing 4.0
processing 5.0
processing 6.0
processing 7.0
processing 8.0
processing 9.0
processing 10.0
processing 11.0
processing 12.0
processing 13.0
processing 15.0
processing 16.0
processing 18.0
processing 20.0


In [7]:
fig = px.line(df_all_filtered, x="creation_timestamp", y="diff_1_std", color = "system_name")
fig.show()
fig = px.line(df_all_filtered, x="creation_timestamp", y="diff_1", color = "system_name")
fig.show()
fig = px.line(df_all_filtered, x="creation_timestamp", y="diff_2", color = "system_name")
fig.show()

fig = px.scatter(df_all_filtered, x="system_name", y=["rmse_1_std_full_deployment", "rmse_mean_deployment","rmse_median_deployment"])
fig.show()